In [1]:
import numpy as np
from knightian_model.discrete import Household, Firm, KnightianInnovationModel


def run_experiment(model):
    model.solve_household_DP_problem()
    model.plot_policy_function(height=2000, width=900, renderer=None)
    popu = model.compute_stationary_distribution()
    model.plot_stationary_distribution(popu, height=1400, width=900, renderer=None)

## Default

In [2]:
hh = Household()
firm = Firm()
model = KnightianInnovationModel(hh, firm)
model.hh.ζ_vals

array([1., 5.])

In [3]:
run_experiment(model)

Running Value Iteration
----------------------------
Iteration 1 : max bellman error is 0.45318667146573827
Iteration 20 : max bellman error is 0.024855586038182276
Iteration 40 : max bellman error is 0.0028322602727355317
Iteration 60 : max bellman error is 0.000334079707797974
Iteration 80 : max bellman error is 3.990027023248466e-05
Iteration 100 : max bellman error is 4.795539102042667e-06
Iteration 120 : max bellman error is 5.785240193567631e-07
Iteration 140 : max bellman error is 6.995823942368418e-08

Converged after 159 iterations.


## Discrete Normal

In [4]:
from scipy import optimize, stats

def discrete_normal(width, μ, σ, num):
    norm_cdf = stats.norm(μ, σ).cdf
    pts = np.linspace(μ - width * σ, μ + width * σ, num=num)
    pts = pts.reshape((-1, 1))  # Chosen to match C-order

    probs = np.zeros(pts.shape)
    probs[0] = norm_cdf((pts[0] + pts[1]) / 2)
    for i in range(1, num - 1):
        probs[i] = (norm_cdf((pts[i+1] + pts[i]) / 2) -
                    norm_cdf((pts[i] + pts[i-1]) / 2))
    probs[-1] = 1 - probs[:-1].sum()

    μ_pts = probs.T @ pts
    σ_pts = np.sqrt(probs.T @ pts ** 2 - μ_pts ** 2)

    error = (σ_pts - σ).item()

    return np.abs(error), pts, probs


μ = 3.
σ = 1.
num = 5
args = (μ, σ, num)

x0 = 1.
res = optimize.root(lambda x, *args: discrete_normal(x, *args)[0],
                             x0, args=args)

if res.success:
    width = res.x
    _, y_grid, y_dist = discrete_normal(width, *args)
else: 
    print('Failed to create income grid.')

ζ_vals = y_grid.flatten()
P_ζ = np.ones((num, num)) * y_dist.T

hh_norm = Household(ζ_vals=ζ_vals, P_ζ=P_ζ)
firm_norm = Firm()
model_norm = KnightianInnovationModel(hh_norm, firm)
model_norm.hh.ζ_vals

array([1.06626942, 2.03313471, 3.        , 3.96686529, 4.93373058])

In [5]:
run_experiment(model_norm)

Running Value Iteration
----------------------------
Iteration 1 : max bellman error is 0.42502079184302693
Iteration 20 : max bellman error is 0.024816270910891225
Iteration 40 : max bellman error is 0.0029954667628935283
Iteration 60 : max bellman error is 0.0003630956451901035
Iteration 80 : max bellman error is 4.407961172248065e-05
Iteration 100 : max bellman error is 5.355014468966246e-06
Iteration 120 : max bellman error is 6.507828518298453e-07
Iteration 140 : max bellman error is 7.910261978771871e-08
Iteration 160 : max bellman error is 9.615860108169727e-09

Converged after 160 iterations.
